In [1]:
import pandas as pd
import numpy as np
from numpy.lib.stride_tricks import sliding_window_view
import os
import json

# python script imports
import mimic_diagnoses
import preprocessing
import models

# reload the files every time
print(os.getcwd())
import importlib
importlib.reload(mimic_diagnoses)
importlib.reload(preprocessing)
importlib.reload(models)

patients = pd.read_csv('mimic_data/PATIENTS.csv')
admissions = pd.read_csv('mimic_data/ADMISSIONS.csv')
diagnoses = pd.read_csv('mimic_data/DIAGNOSES_ICD.csv')

admissions_leadii, patients_leadii, diagnoses_leadii = mimic_diagnoses.get_leadii_dataframes(patients, admissions, diagnoses)
ethnicities_leadii = admissions_leadii.drop_duplicates(subset='SUBJECT_ID')
ethnicities_leadii['ETHNICITY_COND'] = ethnicities_leadii.ETHNICITY.apply(lambda x: mimic_diagnoses.get_race(x))

mimic_diagnoses.add_icd_10_code_to_diagnoses(diagnoses_leadii)

# getting features and labels for three different scenarios
data_dictionary, start_times = preprocessing.get_aligned_ss_and_bp(admissions_leadii, True)
patient_ids = np.array([tup[0] for tup in list(data_dictionary.keys())])


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
/Users/luismendoza/Desktop/CS/HMC CS/Clinic/EIT-Clinic-Waveform/sleep/risk_classification


/var/folders/dd/qg8x4_x12xz7xhhxct81hxrh0000gn/T/ipykernel_66738/325045391.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ethnicities_leadii['ETHNICITY_COND'] = ethnicities_leadii.ETHNICITY.apply(lambda x: mimic_diagnoses.get_race(x))
/Users/luismendoza/Desktop/CS/HMC CS/Clinic/EIT-Clinic-Waveform/sleep/risk_classification/mimic_diagnoses.py:66: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  diagnoses['ICD10_CODE'] = diagnoses.ICD9_CODE.apply(lambda x: icd_9_to_10_from_code(x, icd_9_to_10_d))


In [2]:
start_before_sleep_arrays = []
sleep_start_indices = []
for bp_ss in list(data_dictionary.values()):
    start_before_sleep_array, sleep_start = preprocessing.get_start_before_sleep(bp_ss, True)
    start_before_sleep_arrays.append(start_before_sleep_array)
    sleep_start_indices.append(sleep_start)

start_before_sleep_arrays_bp_meaned = []
for arr in start_before_sleep_arrays:
    sbp = arr[0]
    dbp = arr[1]
    ss = arr[2]
    try:
        sbp_means = np.pad(np.apply_along_axis(lambda x: np.mean(x), 1, sliding_window_view(sbp, 60)), (30, 29), 'edge')
        dbp_means = np.pad(np.apply_along_axis(lambda x: np.mean(x), 1, sliding_window_view(dbp, 60)), (30, 29), 'edge')
    except:
        sbp_means = sbp
        dbp_means = dbp

    arr_means = np.concatenate((sbp_means.reshape((1,-1)),dbp_means.reshape((1,-1)),ss.reshape((1,-1))),axis=0)
    start_before_sleep_arrays_bp_meaned += [arr_means]

/Users/luismendoza/Desktop/CS/HMC CS/Clinic/EIT-Clinic-Waveform/sleep/risk_classification/preprocessing.py:227: RuntimeWarning: invalid value encountered in scalar divide
  if np.sum(ss[sleep_start:end] == 3) / len(ss[sleep_start:end]) >= 0.5:


In [3]:
print(start_before_sleep_arrays)


[array([], shape=(3, 0), dtype=float64), array([[109.68767139, 108.75016992, 106.87516699, ..., 168.28151294,
        170.6252666 , 171.56276807],
       [ 67.50010547,  67.03135474,  66.562604  , ...,  73.12511426,
         76.87512012,  78.04699695],
       [  3.        ,   3.        ,   3.        , ...,   3.        ,
          3.        ,   3.        ]]), array([], shape=(3, 0), dtype=float64), array([], shape=(3, 0), dtype=float64), array([], shape=(3, 0), dtype=float64), array([[136.70152327, 133.37687965, 133.96358146, 134.35471601,
        133.47466328, 135.1369851 , 132.10569238, 132.79017783,
        132.39904328, 128.87883239, 129.07439966, 128.87883239,
        128.97661602, 126.43424148, 128.0965633 , 132.59461056,
        129.07439966, 135.82147055, 134.55028328, 131.03007238,
        129.85666875, 129.4655342 , 127.70542875, 135.430336  ,
        139.04833054, 137.77714327, 133.08352874, 136.70152327,
        136.31038873, 137.48379236, 136.70152327, 132.79017783,
       

In [4]:
min_num_hours = 6
fixed_block_hours = 6
has_min_hours = np.array([len(arr[0]) for arr in start_before_sleep_arrays]) > min_num_hours*60*2
    
# zero pad / cut off for a minimum hour block
X = preprocessing.pad_list_of_arrays(start_before_sleep_arrays, fixed_block_hours*60*2)
X = X[has_min_hours]

nan_mask = np.isnan(X).any(axis=(1,2))
X = X[~nan_mask]



print(has_min_hours)

for i in range(len(has_min_hours)):
    if  not has_min_hours[i]:
        sleep_start_indices[i] = -2
        
cleaned_list = [x for x in sleep_start_indices if x != -2]
sleep_start_indices = cleaned_list

for i in range(len(nan_mask)):
    if nan_mask[i]:
        sleep_start_indices[i] = -2

cleaned_list = [x for x in sleep_start_indices if x != -2]
sleep_start_indices = cleaned_list

print(len(sleep_start_indices))

[False  True False False False False False False False  True False  True
  True False  True False False  True False  True False False False False
 False False False False False False False False  True False  True  True
 False False  True False False False False False  True  True False False
 False False False  True False  True  True  True False  True False False
 False False  True  True False False False False False False  True  True
 False False  True  True  True False False  True False False  True False
 False False False  True False False False False False False False False
 False False False False False False False False False False  True False
 False False False False False False  True False  True False False False
 False False False False False False False False False False False  True
 False False False False False False False False False False  True  True
  True  True False False  True  True  True False False False False False
 False False False  True False False False False Fa

In [5]:
print(len(start_times))
for i in range(len(has_min_hours)):
    if  not has_min_hours[i]:
        start_times[i] = -2
        
cleaned_list = [x for x in start_times if x != -2]
start_times = cleaned_list

for i in range(len(nan_mask)):
    if nan_mask[i]:
        start_times[i] = -2

cleaned_list = [x for x in start_times if x != -2]
start_times = cleaned_list
print(len(start_times))

700
121


In [6]:
print("got sleep starts")
X_sum, y_sum, patient_ids_sum = preprocessing.get_features(patient_ids, start_before_sleep_arrays, True, True, False, patients, admissions, diagnoses_leadii, 8)
print("sum")
X_sum_dem, y_sum_dem, patient_ids_sum_dem = preprocessing.get_features(patient_ids, start_before_sleep_arrays, True, True, True, patients, admissions, diagnoses_leadii, 8)
print("sum dem")
X_ts, y_ts, patient_ids_ts = preprocessing.get_features(patient_ids, start_before_sleep_arrays, False, True, False, patients, admissions, diagnoses_leadii, 6, 6)
print("ts")

got sleep starts
sum
sum dem
[False  True False False False False False False False  True False  True
  True False  True False False  True False  True False False False False
 False False False False False False False False  True False  True  True
 False False  True False False False False False  True  True False False
 False False False  True False  True  True  True False  True False False
 False False  True  True False False False False False False  True  True
 False False  True  True  True False False  True False False  True False
 False False False  True False False False False False False False False
 False False False False False False False False False False  True False
 False False False False False False  True False  True False False False
 False False False False False False False False False False False  True
 False False False False False False False False False False  True  True
  True  True False False  True  True  True False False False False False
 False False False  Tr

In [7]:
print(len(X_ts))
print(len(patient_ids_ts))
print(len(sleep_start_indices))

121
121
121


In [8]:
print(X_ts[0][0][0])

145.0669896890096


In [9]:
print(X_ts[0][0][479])


127.28773573385826


In [10]:
print(sleep_start_indices)
print(start_times)

[80, 99, 476, 1427, 62, 88, 352, 39, 153, 22, 80, 80, 174, 350, 39, 95, 491, 17, 254, 851, 50, 161, 94, 1, 2150, 169, 24, 108, 653, 250, 32, 33, 70, 106, 883, 211, 244, 98, 75, 159, 370, 995, 91, 45, 53, 483, 40, 41, 221, 48, 339, 65, 288, 29, 897, 329, 35, 274, 395, 8, 371, 592, 48, 662, 52, 41, 91, 377, 1347, 920, 230, 297, 437, 140, 205, 1475, 195, 2725, 41, 248, 149, 55, 952, 267, 729, 380, 85, 58, 237, 51, 78, 358, 21, 62, 90, 1109, 120, 347, 71, 62, 101, 37, 148, 118, 88, 85, 552, 37, 1053, 161, 13, 164, 136, 126, 393, 83, 272, 494, 165, 15, 573]
['22', '20', '17', '10', '10', '10', '01', '17', '18', '13', '13', '12', '11', '15', '15', '15', '15', '15', '12', '12', '15', '17', '16', '16', '12', '00', '12', '22', '15', '17', '14', '14', '14', '14', '20', '15', '15', '15', '15', '19', '15', '15', '15', '10', '17', '17', '12', '17', '16', '13', '16', '01', '13', '00', '14', '18', '18', '09', '14', '11', '11', '11', '11', '11', '11', '07', '11', '10', '15', '11', '11', '14', '12', '0

In [11]:
def find_index_at_time(start_time, desired_time):
    if desired_time < start_time:
        time_diff = (24-start_time) + desired_time
    else:
        time_diff = desired_time - start_time
    
    epochs_per_hour = (3600 / 30)
    desired_index = time_diff * epochs_per_hour
    
    return int(desired_index)

In [12]:
dimensions = (len(X_ts), 3, 4)
X_four = np.zeros(dimensions)
for patient in range(len(X_ts)):
    for data_type in range(len(X_ts[patient])):
        index_at_2 = find_index_at_time(int(start_times[patient]), 2)
        index_at_4 = find_index_at_time(int(start_times[patient]), 4)
        print(patient, data_type)
        if index_at_2 >= len(X_ts[patient][data_type]):
            index_at_2 = len(X_ts[patient][data_type])-1
            print("2 am not existent")
        if index_at_4 >= len(X_ts[patient][data_type]):
            index_at_4 = len(X_ts[patient][data_type])-1
            print("4 am not existent")
        X_four[patient][data_type][0] = X_ts[patient][data_type][0]
        X_four[patient][data_type][1] = X_ts[patient][data_type][index_at_2]
        X_four[patient][data_type][2] = X_ts[patient][data_type][index_at_4]
        X_four[patient][data_type][3] = X_ts[patient][data_type][479]

0 0
4 am not existent
0 1
4 am not existent
0 2
4 am not existent
1 0
2 am not existent
4 am not existent
1 1
2 am not existent
4 am not existent
1 2
2 am not existent
4 am not existent
2 0
2 am not existent
4 am not existent
2 1
2 am not existent
4 am not existent
2 2
2 am not existent
4 am not existent
3 0
2 am not existent
4 am not existent
3 1
2 am not existent
4 am not existent
3 2
2 am not existent
4 am not existent
4 0
2 am not existent
4 am not existent
4 1
2 am not existent
4 am not existent
4 2
2 am not existent
4 am not existent
5 0
2 am not existent
4 am not existent
5 1
2 am not existent
4 am not existent
5 2
2 am not existent
4 am not existent
6 0
6 1
6 2
7 0
2 am not existent
4 am not existent
7 1
2 am not existent
4 am not existent
7 2
2 am not existent
4 am not existent
8 0
2 am not existent
4 am not existent
8 1
2 am not existent
4 am not existent
8 2
2 am not existent
4 am not existent
9 0
2 am not existent
4 am not existent
9 1
2 am not existent
4 am not existent
9 

In [13]:
print(X_four)

[[[145.06698969 129.1926558  146.63000103 127.28773573]
  [ 75.92816009  67.84446083  71.94736559  66.86757875]
  [  3.           1.           3.           1.        ]]

 [[160.96574563 164.99538423 164.99538423 152.24707302]
  [ 89.43355492  75.07338827  75.07338827  69.50516038]
  [  3.           1.           1.           1.        ]]

 [[156.0000624  144.0000576  144.0000576  111.60004464]
  [ 69.60002784  55.20002208  55.20002208  64.80002592]
  [  3.           1.           1.           1.        ]]

 ...

 [[ 84.         148.8        148.8        132.8       ]
  [ 52.8         58.4         58.4         52.8       ]
  [  3.           1.           1.           1.        ]]

 [[130.8        104.          96.         104.8       ]
  [ 64.          75.2         60.8         75.6       ]
  [  3.           3.           1.           3.        ]]

 [[121.875      109.375      109.375      121.875     ]
  [ 58.203125    47.65625     47.65625     67.96875   ]
  [  3.           2.           2

In [15]:
os.environ['LC_ALL'] = 'en_US.UTF-8'
os.environ['LANG'] = 'en_US.UTF-8'

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Process SpawnPoolWorker-13117:
Traceback (most recent call last):
  File "/Users/luismendoza/opt/anaconda3/lib/python3.9/multiprocessing/process.py", line 315, in _bootstrap
    self.run()
  File "/Users/luismendoza/opt/anaconda3/lib/python3.9/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/luismendoza/opt/anaconda3/lib/python3.9/multiprocessing/pool.py", line 114, in worker
    task = get()
  File "/Users/luismendoza/opt/anaconda3/lib/python3.9/multiprocessing/queues.py", line 367, in get
    return _ForkingPickler.loads(res)
ModuleNotFoundError: No module named 't2f'


In [14]:
# calculate features
X_ts_feats = models.calculate_features(X_ts)
X_ts_meaned_feats = models.calculate_features(X_ts_meaned)

supervised_accuracies, all_models_dict = models.get_selected_features_and_scores_over_n_runs(10, X_ts_feats, y_ts, 0.5)

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

/Users/luismendoza/opt/anaconda3/lib/python3.9/multiprocessing/resource_tracker.py:96: UserWarning: resource_tracker: process died unexpectedly, relaunching.  Some resources might leak.
  warnings.warn('resource_tracker: process died unexpectedly, '
Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

...

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) fa

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized

Fatal Python error: config_get_locale_encoding: failed to get the locale encoding: nl_langinfo(CODESET) failed
Python runtime state: preinitialized



KeyboardInterrupt: 

In [22]:
X_four.shape

(121, 3, 4)

In [23]:
X_four_reshaped = X_four.reshape(X_four.shape[0], -1)

In [24]:
X_four_reshaped.shape

(121, 12)

In [26]:
models.score_summary_model(X_four_reshaped, y_ts, model_type="svc", test_size=0.2)

(52.0,
 36.36363636363637,
 64.28571428571429,
 35.714285714285715,
 63.63636363636363)

In [28]:
models.cross_validate_summary_model_with_smote(X_four_reshaped, y_ts, model_type="svc", oversampling_method="smote")

{'fit_time': array([0.04662871, 0.00177217, 0.00143981, 0.00142169, 0.00167799]),
 'score_time': array([0.0019803 , 0.00041604, 0.00040507, 0.00039315, 0.00058198]),
 'test_score': array([0.36      , 0.33333333, 0.375     , 0.16666667, 0.25      ])}

In [31]:
models.cross_validate_summary_model(X_four_reshaped, y_ts, model_type="svc")

{'fit_time': array([0.0015471 , 0.00080085, 0.00058699, 0.00055003, 0.00055313]),
 'score_time': array([0.00066686, 0.00044703, 0.00039697, 0.00037289, 0.00048995]),
 'test_score': array([0.52      , 0.20833333, 0.54166667, 0.16666667, 0.41666667])}

In [32]:
models.cross_validate_summary_model(X_four_reshaped, y_ts, model_type="rfc")

{'fit_time': array([0.10866714, 0.08368182, 0.06909108, 0.06752205, 0.06575203]),
 'score_time': array([0.00848079, 0.00340915, 0.00337481, 0.00320578, 0.00312924]),
 'test_score': array([0.56      , 0.375     , 0.54166667, 0.20833333, 0.5       ])}

In [33]:
models.cross_validate_summary_model(X_four_reshaped, y_ts, model_type="knc")

{'fit_time': array([0.00457907, 0.0007391 , 0.00042796, 0.00045109, 0.00053668]),
 'score_time': array([0.00882602, 0.00295591, 0.0024209 , 0.00258017, 0.00261211]),
 'test_score': array([0.36      , 0.33333333, 0.45833333, 0.08333333, 0.41666667])}

In [35]:
models.compare_averages_summary_models(X_four_reshaped, y_ts)

(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363636363)
(52.0, 36.36363636363637, 64.28571428571429, 35.714285714285715, 63.63636363

(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
(36.0, 54.54545454545455, 21.428571428571427, 78.57142857142857, 45.45454545454545)
knc averaged summary accuracies: [36.         54.54545455 21.42857143 78.571